# Zed-Odds Sample Notebook 

This notebook is intended to help you load zed-odds data, merge the data and see it for your horses.

*Note: The very first time you use this you may need to install some of the below packages using pip install or conda.*

#### You are welcome to use this for free - if you publish data please give credit to Hawku or @hawku_com on twitter.  Also contributions and additions are welcome - contact @cryptog#4364

In [1]:
import numpy as np
import pandas as pd  # To read data
from pandas.io.json import json_normalize
import requests
from datetime import datetime
from io import StringIO
pd.set_option("display.max_rows", 200)
pd.set_option('display.max_columns', 100)



In [2]:
folder = "../zed_odds/"

horses = pd.read_csv(f"{folder}/horse_db.csv")
races = pd.read_csv(f"{folder}/race_db.csv")
horse_race_data_since_aug_1 = pd.read_csv(f"{folder}/horse_race_data_db.csv")
horse_race_data_before_aug_1 = pd.read_csv(f"{folder}/horse_race_data_db_before_08_01_21.csv") 

### ENTER YOUR STABLE'S WALLET AND YOUR PRIVATE ZED API KEY HERE to use things for your stable

In [17]:
wallet_address = "YOUR WALLET ADDRESS"
private_api_key = "YOUR ZED PRIVATE API KEY AFTER BEARER"

### Combine the two horse race data files

In [4]:
horse_race_data = horse_race_data_since_aug_1.append(horse_race_data_before_aug_1)

### Example of merging races with horse data 

In [5]:
races_with_horse_race_data = races.merge(horse_race_data, left_on="race_id",  right_on = "race_id")

In [6]:
races_with_horse_race_data.head()

race_id           start_time                  name  distance  class  \
0  3SQvsynO  2021-08-01 23:21:38  Stavanger Grand Prix      2000      3   
1  3SQvsynO  2021-08-01 23:21:38  Stavanger Grand Prix      2000      3   
2  3SQvsynO  2021-08-01 23:21:38  Stavanger Grand Prix      2000      3   
3  3SQvsynO  2021-08-01 23:21:38  Stavanger Grand Prix      2000      3   
4  3SQvsynO  2021-08-01 23:21:38  Stavanger Grand Prix      2000      3   

  country       city weather     fee  prize_pool_first  prize_pool_second  \
0  Norway  Stavanger   Sunny  0.0098          0.063504            0.02646   
1  Norway  Stavanger   Sunny  0.0098          0.063504            0.02646   
2  Norway  Stavanger   Sunny  0.0098          0.063504            0.02646   
3  Norway  Stavanger   Sunny  0.0098          0.063504            0.02646   
4  Norway  Stavanger   Sunny  0.0098          0.063504            0.02646   

   prize_pool_third  horse_id   odds  fire  place  horse_time  gate  
0          0.015876     34750   7.39     1      1    119.4445   8.0  
1          0.015876      5629   8.59     1      3    120.4453  11.0  
2          0.015876     37136   8.08     1     10    121.3957  12.0  
3          0.015876     26460  15.40     0      2    120.2405   9.0  
4          0.015876     65204  18.20     0      4    120.7958  10.0

### Do your own analysis using Pandas.  Example of getting mean and std of times by distance

In [7]:
races_with_horse_race_data.groupby("distance").agg(mean_time=("horse_time", "mean"), std_time=("horse_time", "std"))

mean_time  std_time
distance                      
1000       57.718974  0.854620
1200       71.412511  1.072705
1400       83.617551  1.279275
1600       95.776735  1.464007
1800      107.880635  1.635949
2000      119.914868  1.867106
2200      131.979796  2.144134
2400      143.978752  2.502928
2600      156.061063  2.927476

## Example of loading your stable and getting race data for your stable

In [8]:
header = { "authorization": f"Bearer {private_api_key}"}

def get_stable(address):

    stable = requests.get(url=f"https://api.zed.run/api/v1/horses/get_user_horses?public_address={address}&offset=0&gen[]=1&gen[]=268&horse_name=&sort_by=created_by_desc", headers=header).json()
    stable_df = pd.DataFrame(stable)

    offset = len(stable_df)
    while True:
        stable = requests.get(url=f"https://api.zed.run/api/v1/horses/get_user_horses?public_address={address}&offset={offset}&gen[]=1&gen[]=268&horse_name=&sort_by=created_by_desc", headers=header).json()
        stable_df = stable_df.append(stable)
        if(len(stable) < 10):
            break
        offset += 10
    return stable_df
        

## Get all race data for your stable

In [9]:
my_stable = get_stable(wallet_address)

In [10]:
my_stable_with_horse_name = my_stable.merge(horses[["horse_id", "name"]], left_on="horse_id", right_on="horse_id")

In [11]:
my_stable_with_horse_name.columns

Index(['bloodline', 'breed_type', 'breeding_counter', 'breeding_cycle_reset',
       'career', 'class', 'current_fatigue', 'genotype', 'hash_info',
       'horse_id', 'horse_type', 'img_url', 'is_approved_for_racing',
       'is_being_transferred', 'is_in_stud', 'is_on_racing_contract',
       'is_running_free_race', 'last_stud_duration', 'last_stud_timestamp',
       'mating_price', 'number_of_races', 'owner', 'rating', 'super_coat',
       'tx', 'tx_date', 'win_rate', 'name'],
      dtype='object')

In [12]:
my_stable_race_data = races_with_horse_race_data.merge(my_stable_with_horse_name[["horse_id", "name"]], left_on="horse_id", right_on="horse_id")

#### save your stable data to CSV

In [13]:
my_stable_race_data.to_csv("my_stables_races.csv")